In [1]:
import geemap
import ee

# Earth Engine 인증
# ee.Authenticate()

# Earth Engine 초기화
ee.Initialize()

In [3]:
# FAO GAUL(Global Administrative Unit Layers) 2015
countries = ee.FeatureCollection("FAO/GAUL/2015/level0")

# 'ADM0_NAME' 필드를 기준으로 '대한민국' 필터링
kr = countries.filter(ee.Filter.eq('ADM0_NAME', 'Republic of Korea'))

# 지도 생성
Map = geemap.Map()

# 지도에 경계 표시
Map.centerObject(kr, 7) # 경계 중심으로 지도 확대
Map.addLayer(kr, {}, "Republic of Korea")

# 지도 출력
Map

Map(center=[36.34449219000809, 127.80177597242088], controls=(WidgetControl(options=['position', 'transparent_…

In [6]:
# Terra Vegetation Continuous Fields Yearly Global 250m
MODIS = ee.ImageCollection('MODIS/006/MOD44B')

# 날짜 필터링 및 녹지 지수 선택
filtered_MODIS = MODIS.filterDate('2003-01-01', '2020-12-31')
selected_MODIS = filtered_MODIS.select('Percent_Tree_Cover')

# 녹지 지수의 중앙값 계산
MedianPTC = selected_MODIS.median()
visParams = {
    'min': 0,
    'max': 100,
    'palette': ['bbe029', '0a9501', '074b03']}

# 지도 생성
Map = geemap.Map()

Map.centerObject(kr, 7) # 경계 중심으로 지도 확대
Map.addLayer(MedianPTC, visParams, 'Percent Tree Cover')
Map

Map(center=[36.34449219000809, 127.80177597242088], controls=(WidgetControl(options=['position', 'transparent_…

In [8]:
# 대한민국 영역으로 잘라내기
MedianPTC_kr = MedianPTC.clipToCollection(kr)

# 데이터를 GeoTIFF 형식으로 저장
output_file = 'D:/GEODATA/pct_tree_cover.tif'
geemap.ee_export_image(MedianPTC_kr, filename=output_file, region=kr.geometry(), scale=250)

Generating URL ...
An error occurred while downloading.
Total request size (62127918 bytes) must be less than or equal to 50331648 bytes.


In [9]:
# 데이터를 Google Drive에 저장
geemap.ee_export_image_to_drive(
    MedianPTC_kr,
    description='pct_tree_cover',
    folder='export',
    region=kr.geometry(),
    scale=250
)